In [1]:
import numpy as np
import math
import matplotlib as plt
import scipy as sci
from scipy import constants
import pandas as pd
import csv
import math
from numpy import linspace, zeros

In [2]:
G = constants.G
c = constants.c
pi = constants.pi
print(pi, G, c)

3.141592653589793 6.6743e-11 299792458.0


In [3]:
#Read the text file of eos
eos_arr = np.loadtxt('eosaapr.txt', dtype = "str", delimiter = ',')
print("OK")
#Now, to convert this 1D arry of strings to 2D array of floats
#make the three arrays
P = np.zeros(len(eos_arr))
m = np.zeros(len(eos_arr))
e = np.zeros(len(eos_arr))
x = np.zeros(len(eos_arr))
for idx in range(len(eos_arr)):
    input_string = eos_arr[idx]
    str_values = input_string.split()
    float_values = [float(value) for value in str_values]
    #print(float_values)
    #eos_arr[i] = float_values
    P[idx], e[idx], x[idx] = float_values
    print(P[idx], e[idx], x[idx])
print(len(eos_arr))

OK
1.886475e-19 7.378815e-12 7.92406e-15
1.202873e-18 2.333386e-11 2.505808e-14
7.669881e-18 7.378816e-11 7.92406e-14
4.890546e-17 2.333387e-10 2.505808e-13
3.118359e-16 7.37882e-10 7.92406e-13
1.988359e-15 2.333389e-09 2.505808e-12
1.267837e-14 7.378836e-09 7.92406e-12
8.084112e-14 2.333399e-08 2.505808e-11
5.154673e-13 7.378899e-08 7.92406e-11
3.286774e-12 2.33344e-07 2.505808e-10
1.44678e-11 5.86125e-07 6.294102e-10
6.088583e-11 1.472362e-06 1.581048e-09
2.441051e-10 3.698637e-06 3.971469e-09
3.282405e-10 4.656005e-06 4.99938e-09
8.956552e-10 9.289166e-06 9.97366e-09
2.392367e-09 1.853925e-05 1.990382e-08
6.278949e-09 3.700156e-05 3.972096e-08
1.625287e-08 7.382663e-05 7.924186e-08
4.166825e-08 0.0001473225 1.581014e-07
5.453823e-08 0.0001854761 1.990332e-07
1.01674e-07 0.0002940527 3.154997e-07
1.89055e-07 0.00046603 4.999341e-07
2.577115e-07 0.0005868276 6.294586e-07
3.143219e-07 0.0006803509 7.297275e-07
4.281669e-07 0.0009007277 9.659711e-07
7.939188e-07 0.001427997 1.53107e-06


In [4]:
#--converted to SI units MeV/fm^3 to Pa=J/m^2
factor = 1.60218e+32   
P = factor*P 
e = factor*e
for idx in range(len(eos_arr)):
    print(P[idx], " ", e[idx], " ", x[idx])

30224725155000.0   1.1822189816700003e+21   7.92406e-15
192721906314000.03   3.73850438148e+21   2.505808e-14
1228852994058000.0   1.182219141888e+22   7.92406e-14
7835534990280000.0   3.73850598366e+22   2.505808e-13
4.99617242262e+16   1.18221978276e+23   7.92406e-13
3.18570902262e+17   3.73850918802e+23   2.505808e-12
2.03130308466e+18   1.1822223462480001e+24   7.92406e-12
1.295220256416e+19   3.73852520982e+24   2.505808e-11
8.25871398714e+19   1.1822324399820002e+25   7.92406e-11
5.26600356732e+20   3.7385908992000003e+25   2.505808e-10
2.3180019804e+21   9.390777525000002e+25   6.294102e-10
9.755005910940002e+21   2.3589889491600003e+26   1.581048e-09
3.91100309118e+22   5.9258822286600005e+26   3.971469e-09
5.2590036429e+22   7.459758090900001e+26   4.99938e-09
1.435000848336e+23   1.488291598188e+27   9.97366e-09
3.83300256006e+23   2.9703215565e+27   1.990382e-08
1.006000650882e+24   5.92831594008e+27   3.972096e-08
2.6040023256600006e+24   1.182835500534e+28   7.924186e-08
6

In [5]:
def RK4_step(dy_dr, dz_dr, yi, zi, r, h):
    
    K1 = dy_dr(r, yi,  zi)
    L1 = dz_dr(r, yi , zi)
    #print("K1 and L1 done", K1, L1)
    #print(K1, L1)
    K2 = dy_dr(r + h/2, yi + h*K1/2, zi + h*L1/2)
    L2 = dz_dr(r + h/2, yi + h*K1/2, zi + h*L1/2)
    #print("K2 and L2 are done",K2, L2)
    #print("here is the der. ", dz_dr(r + h/2, yi + h*K1/2, zi + h*L1/2))
    K3 = dy_dr(r + h/2, yi + h*K2/2, zi + h*L2/2)
    L3 = dz_dr(r + h/2, yi + h*K2/2, zi + h*L2/2)
    #print("K3 and L3 are done", K3, L3)
    #print(dz_dr(r + h/2, yi + h*K2/2, zi + h*L2/2))
    K4 = dy_dr(r + h, yi + h*K3, zi + h*L3)
    L4 = dz_dr(r + h, yi + h*K3, zi + h*L3)
    #print("K4 and L4 are done", K4, L4)
    yi = yi + h*(K1 + 2*K2 + 2*K3 + K4)/6
    zi = zi + h*(L1 + 2*L2 + 2*L3 + L4)/6
    #print(yi, zi)
    return(yi, zi)

In [6]:
#Interpolation Code, for P 
# three arguments : P  and e are the arrays and temp is the value of density for which the pressure has to be found
def interpolate_P(temp, P, e):
    Pr = 0
    for idx in range(len(P)-1):
        #print(temp, " , ", e[idx])
        if (temp == e[idx]):
            Pr = P[idx]
            #print(Pr)
        elif(e[idx + 1] >= temp >= e[idx]):
            Pr = P[idx] + (temp-e[idx])*(P[idx + 1] - P[idx])/(e[idx + 1] - e[idx])
            #print(Pr)
#         else:
#             Pr = 0
#             print("Error, could not interpolate pressure")
#             break
    return Pr

def interpolate_e(temp, P, e):
    er = 0
    for idx in range(len(P)-1):
        #print(temp, " , ", P[idx])
        if (temp == P[idx]):
            er = e[idx]
            #print(er)
        elif(P[idx + 1] >= temp >= P[idx]):
            er = e[idx] + (temp-P[idx])*(e[idx + 1] - e[idx])/(P[idx + 1] - P[idx])
            #print(er)
#         else:
#             er = 0
#             print("Error, could not interpolate density")
#         break
    return er
            

In [7]:
#interpolation function check
    
epsi = 901*1.60218e+32 #SI units
print(interpolate_P(epsi,P,e))

5.272219567213787e+34


In [18]:
#####################################
#define the derivative function to get dm/dr and dP/dr
def dm_dr(r, m_r, P_r):
    #e_r = interpolate_e(P_r, P, e)
    #print("inputs:", r, m_r, P_r, e_r)
    mprime = 4*pi*e_r*(r**2)/c**2
    print("mprime:", mprime, "*********")
    return mprime

def dP_dr_nat(r, m_r, P_r):
    #e_r = interpolate_e(P_r, P, e)
    Pprime = -(e_r + P_r)*((m_r + 4*pi*(r**3)*P_r)/(r*r - 2*m_r*r))
    return Pprime

# def dP_dr_units(r, m_r, P_r):
#     e_r = interpolate_e(P_r, P, e)
#     Pprime = -(G/r*c**2)*(e_r + P_r)*((m_r*c**2 + 4*pi*r**3*P_r)/(r*c**2 - 2*G*m_r))
#     print("****", Pprime, "*********")
#     return Pprime

def dP_dr_units(r, m_r , P_r):
    #e_r = interpolate_e(P_r, P, e)
    #print("inputs:", r, m_r, P_r, e_r)
    Pprime = -(G*m_r/(r**2*c**2))*(e_r + P_r)*(1 + 4*pi*r**3*P_r/(m_r*c**2))*((1 - 2*G*m_r/(r*c**2))**(-1))
    print("Pprime:", Pprime, "*********")
    return Pprime
#print(Pprime(ri, mi, pi))
######################################




In [19]:
#calculating a central mass for a small radius of constant density
epsi = 1000*1.60218e+32 #SI units
#epsi = 4e+34 * 7.4237e-19  #natural units
rc = 1.0e-3
m_c = (epsi/c**2)*4/3*pi*rc**3
print("r:", rc)
print("m(c):", m_c)

r: 0.001
m(c): 7467212483.534294


In [20]:
ri = rc
rf = 20000.0
N = 20000
r = linspace(ri, rf, N)
h = r[1] - r[0]
mi = m_c

#2d array for storing mass,pressure and energy density values
y = np.zeros((3,N))

#tov_solver code
for i in range(N):
    #r[i] = r[i]*1000 #for SI units
    if(i == 0):
        y[0][i] = m[0] = mi
        y[1][i] = interpolate_P(epsi,P,e)
        y[2][i] = epsi
        print(i, "  ",r[i], "  ", y[0][i], "  ", y[1][i], " ", y[2][i])
    else:
        if(y[1][i-1] >= 1e-20):
            y[2][i] = e_r = interpolate_e(y[1][i-1],P,e)
            y[0][i], y[1][i] = RK4_step(dm_dr,dP_dr_units, y[0][i-1],y[1][i-1],r[i],h)
            print(i, "  ",r[i], "  ", y[0][i], "  ", y[1][i],"  ", y[2][i])
            if(y[1][i] == 0 or y[2][i] == 0):
                print("error compensated")
        else:
            print(y[1][i-1], "Boundary reached")
            print(i, "  ", r[i], "  ",  y[0][i], "  ", y[1][i], "  ", y[2][i])
            mass = y[0][i-1]/1.989e+30
            radius = r[i-1]/1000
            print("mass:", mass , " $M_{\odot}$ for radius:" , radius, " km")
            break
            if(y[1][i] == 0 or y[2][i] == 0):
                print("error compensated")
            



0    0.001    7467212483.534294    6.768426052127328e+34   1.6021800000000001e+35
mprime: 2.2448703456557842e+19 *********
Pprime: -1.603337118673479e+27 *********
mprime: 5.0475950640505815e+19 *********
Pprime: -3.2473282957224e+27 *********
mprime: 5.0475950640505815e+19 *********
Pprime: -4.29996948351245e+27 *********
mprime: 8.970513559544565e+19 *********
Pprime: -5.338518247920616e+27 *********
1    1.0010499524976249    5.234555493707114e+19    6.7684256848348e+34    1.6021800000000001e+35
mprime: 8.970513352947982e+19 *********
Pprime: -5.417429479058746e+27 *********
mprime: 1.4013625509395099e+20 *********
Pprime: -6.635663482131727e+27 *********
mprime: 1.4013625509395099e+20 *********
Pprime: -7.317896230336185e+27 *********
mprime: 2.0176931417142624e+20 *********
Pprime: -8.423762268074123e+27 *********
2    2.00109990499525    1.943558930332654e+20    6.768424988994857e+34    1.6021799631007848e+35
mprime: 2.017693053678686e+20 *********
Pprime: -8.458845416115916e+27 

In [11]:
np.savetxt( "P_e_APR_tabular.txt", np.c_[r,y[0],y[1]])